In [1]:
import cv2
import numpy as np

import os
from os import listdir
from os.path import isfile, join
import shutil

import matplotlib.pyplot as plt
import matplotlib.image as mpimg

import random

In [2]:
path_temp_folder_images = "data/resumes/temp/"

In [3]:
path_directories = [x[0]  for x in os.walk(path_temp_folder_images)]

#random.shuffle(path_directories)

folder_rectagles = list(filter(lambda x: '_rectangles' in x, path_directories))

print(folder_rectagles)

['data/resumes/temp/images_resumes_77828437.pdf_rectangles', 'data/resumes/temp/images_resumes_19176318.pdf_rectangles', 'data/resumes/temp/images_resumes_23302948.pdf_rectangles', 'data/resumes/temp/images_resumes_47729453.pdf_rectangles', 'data/resumes/temp/images_resumes_26767199.pdf_rectangles', 'data/resumes/temp/images_resumes_15011085.pdf_rectangles', 'data/resumes/temp/images_resumes_22776912.pdf_rectangles', 'data/resumes/temp/images_resumes_17983957.pdf_rectangles', 'data/resumes/temp/images_resumes_11270462.pdf_rectangles', 'data/resumes/temp/images_resumes_14455622.pdf_rectangles', 'data/resumes/temp/images_resumes_38663892.pdf_rectangles', 'data/resumes/temp/images_resumes_93576192.pdf_rectangles', 'data/resumes/temp/images_resumes_27084878.pdf_rectangles', 'data/resumes/temp/images_resumes_25525152.pdf_rectangles', 'data/resumes/temp/images_resumes_21178545.pdf_rectangles', 'data/resumes/temp/images_resumes_23011221.pdf_rectangles', 'data/resumes/temp/images_resumes_96547

In [4]:
def get_files_in_directory(path_directory, extension):

    onlyfiles = [f for f in listdir(path_directory) if isfile(join(path_directory, f))]

    files_names = list(filter(lambda x: '.'+extension in x, onlyfiles))
    
    files_names.sort()
    
    return files_names

In [5]:
def cut_image(path_file_image, path_output_images_folder,path_base_image):
    img = cv2.imread(path_file_image)
    
    base_image = cv2.imread(path_base_image)
    
    heightImage, widthImage, channelsImage = img.shape

    gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
    gray = cv2.bilateralFilter(gray, 11, 17, 17)

    kernel = np.ones((5,5),np.uint8)
    erosion = cv2.erode(gray,kernel,iterations = 1)

    #fig = plt.figure()
    #fig.set_size_inches(10,23)
    #plt.title('erosion')
    #plt.imshow(erosion, cmap='gray', aspect='auto') 
    #plt.show()
    
    kernel = np.ones((4,4),np.uint8)
    dilation = cv2.dilate(erosion,kernel, iterations = 2)

    #fig = plt.figure()
    #fig.set_size_inches(10,23)
    #plt.title('dilation')
    #plt.imshow(dilation, cmap='gray', aspect='auto') 
    #plt.show()

    blurred = cv2.GaussianBlur(gray, (7,7), 3)

    #fig = plt.figure()
    #fig.set_size_inches(10,23)
    #plt.title('blurred')
    #plt.imshow(blurred, cmap='gray', aspect='auto') 
    #plt.show()

    img_thresh = cv2.threshold(blurred, 150, 255, cv2.THRESH_BINARY)[1]
    
    edged = cv2.Canny(img_thresh, 120, 255, 2)

    #fig = plt.figure()
    #fig.set_size_inches(10,23)
    #plt.title('edged')
    #plt.imshow(edged, cmap='gray', aspect='auto') 
    #plt.show()

    # _, contours = cv2.findContours(gray, cv2.RETR_EXTERNAL , cv2.CHAIN_APPROX_SIMPLE)

    #rects = [cv2.boundingRect(cnt) for cnt in _]
    #rects = sorted(rects,key=lambda  x:x[1],reverse=False)

    """ Existe el problema que en los rectangulos toma el borde externo y el interno, con esto solo toma el externo"""
    rects , hierarchy = cv2.findContours(edged, cv2.RETR_TREE, cv2.CHAIN_APPROX_SIMPLE)
    #rects = rects[0] if len(rects) == 2 else rects[1]

    i = -1
    j = 1
    y_old = heightImage
    x_old = widthImage
    area_full_image = widthImage * heightImage
    
    print(f"Altura imagen: {heightImage}")
    print(f"Ancho imagen: {widthImage}")
    print(f"Area imagen: {area_full_image}")
    
    for rect in rects:
        x, y, w, h = cv2.boundingRect(rect)
        # x, y, w, h = rect
        area = w * h
        # print(area)
        
        percentage_area = (100.0 * area) / area_full_image 
        
        if int(area_full_image * 0.015) < area < int(area_full_image * 0.80):

            if (y_old - y) > 200:
                i += 1
                y_old = y
                
                
                
                print(f"Porcetanje Y: {percentage_area} %")

            if abs(x_old - x) > 0:
                x_old = x
                x, y, w, h = cv2.boundingRect(rect)
                # x,y,w,h = rect

                out = base_image[y+10:y+h-10, x+10:x+w-10]

                #cv2.rectangle(image, (x, y), (x + w, y + h), (0, 0, 255), 3)

                #cv2.imshow('out', out)
                #cv2.waitKey(0)

                #cv2.destroyAllWindows()
                
                print(f"Porcetanje X: {percentage_area} %")
                
                if out.any():
                    cv2.imwrite(join(path_output_images_folder,'crop_' + str(j) + '.jpeg'), out)
                    j+=1

In [6]:
for directory in folder_rectagles:
    print("####################")
    print(directory)
    path_directories = [x[0]  for x in os.walk(directory)]

    
    folder_cuts = list(filter(lambda x: 'cuts' in x, path_directories))

    print(folder_cuts)

    #Eliminar carpetas temporales "cuts"

    for dir in folder_cuts:

        if os.path.exists(dir):

            shutil.rmtree(dir)

        else:
            # file not found message
            print("File not found in the directory")

####################
data/resumes/temp/images_resumes_77828437.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_19176318.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_23302948.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_47729453.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_26767199.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_15011085.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_22776912.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_17983957.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_11270462.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_14455622.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_38663892.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_93576192.pdf_rectangles
[]
####################
data/re

[]
####################
data/resumes/temp/images_resumes_10926726.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_26586477.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_18072085.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_12082377.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_35422305.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_24230851.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_15906625.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_19268120.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_11773925.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_16833515.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_18885767.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_18172739.pdf_rectangles
[]
####################
data

[]
####################
data/resumes/temp/images_resumes_11152490.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_19179079.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_22380187.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_21338490.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_28916894.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_20457611.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_24658786.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_10251432.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_89512321.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_15363277.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_38688388.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_88907739.pdf_rectangles
[]
####################
data

[]
####################
data/resumes/temp/images_resumes_61065616.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_32518109.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_18457785.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_33803142.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_53169257.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_14206561.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_36136569.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_14508237.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_46260230.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_38115035.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_28165687.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_14126433.pdf_rectangles
[]
####################
data

[]
####################
data/resumes/temp/images_resumes_27485716.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_29878348.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_83566455.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_16237710.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_25694422.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_36574147.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_29221006.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_98965485.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_18311419.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_26673507.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_17704246.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_21856577.pdf_rectangles
[]
####################
data

[]
####################
data/resumes/temp/images_resumes_29211359.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_20504094.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_14726000.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_86595128.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_32985311.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_18484846.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_91564103.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_22965804.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_14391434.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_22259768.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_27213082.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_35121930.pdf_rectangles
[]
####################
data

[]
####################
data/resumes/temp/images_resumes_27219200.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_36694627.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_28063132.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_23354541.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_10653119.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_20006992.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_94417768.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_17539842.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_15699744.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_16332348.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_17847636.pdf_rectangles
[]
####################
data/resumes/temp/images_resumes_59450123.pdf_rectangles
[]
####################
data

In [7]:
for directory in folder_rectagles:
    print("####################")
    print(directory)
    
    
    pages_images = files_names = get_files_in_directory(directory, "jpeg")
    for page_image in pages_images:
        print(page_image)
        part_name_file = page_image.split(".")
        
        path_base_image = directory.replace("_rectangles","") + "/" + \
        part_name_file[0].replace("_rectangles","").replace("jpeg","pdf") + ".jpeg"
        
        print(path_base_image)
        
        pat_original_image = join(directory,page_image);
        print(pat_original_image)
        
        result_image_restangle_folder = directory + "/cuts_" + part_name_file[0].replace("_rectangles","")
        
        isExistFolder = os.path.exists(result_image_restangle_folder)

        if not isExistFolder:
            print(result_image_restangle_folder)
            os.makedirs(result_image_restangle_folder)
        
        #result_path_image = join(result_image_restangle_folder,part_name_file[0] + "_rectangles.jpeg")
        #print(result_path_image)
        #Process_Image(join(directory,page_image),result_path_image)
        
        cut_image(pat_original_image, result_image_restangle_folder, path_base_image)
        
    #break
    

####################
data/resumes/temp/images_resumes_77828437.pdf_rectangles
1_ENGINEERING_77828437_rectangles.jpeg
data/resumes/temp/images_resumes_77828437.pdf/1_ENGINEERING_77828437.jpeg
data/resumes/temp/images_resumes_77828437.pdf_rectangles/1_ENGINEERING_77828437_rectangles.jpeg
data/resumes/temp/images_resumes_77828437.pdf_rectangles/cuts_1_ENGINEERING_77828437
Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 41.763961798276576 %
Porcetanje X: 41.763961798276576 %
Porcetanje X: 16.07463701277805 %
Porcetanje X: 22.33153572331925 %
Porcetanje Y: 42.663620694906655 %
Porcetanje X: 42.663620694906655 %
Porcetanje X: 7.079972401847116 %
Porcetanje X: 12.498770895602439 %
2_ENGINEERING_77828437_rectangles.jpeg
data/resumes/temp/images_resumes_77828437.pdf/2_ENGINEERING_77828437.jpeg
data/resumes/temp/images_resumes_77828437.pdf_rectangles/2_ENGINEERING_77828437_rectangles.jpeg
data/resumes/temp/images_resumes_77828437.pdf_rectangles/cuts_2_ENGINEERING_77828

Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 15.80550039529984 %
Porcetanje X: 15.80550039529984 %
Porcetanje X: 13.041542569885966 %
Porcetanje Y: 23.910996950165735 %
Porcetanje X: 23.910996950165735 %
Porcetanje X: 20.869919536287465 %
Porcetanje Y: 25.18155568695431 %
Porcetanje X: 25.18155568695431 %
Porcetanje X: 19.61951066250134 %
Porcetanje X: 2.626103628150646 %
Porcetanje Y: 3.2791677647217736 %
Porcetanje X: 3.2791677647217736 %
Porcetanje X: 1.846892824082964 %
Porcetanje Y: 18.910362947493322 %
Porcetanje X: 18.910362947493322 %
Porcetanje X: 2.0182639119719568 %
Porcetanje X: 9.843003225964512 %
2_FINANCE_15011085_rectangles.jpeg
data/resumes/temp/images_resumes_15011085.pdf/2_FINANCE_15011085.jpeg
data/resumes/temp/images_resumes_15011085.pdf_rectangles/2_FINANCE_15011085_rectangles.jpeg
data/resumes/temp/images_resumes_15011085.pdf_rectangles/cuts_2_FINANCE_15011085
Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y:

Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 10.992265498468461 %
Porcetanje X: 10.992265498468461 %
Porcetanje X: 7.2373308719241765 %
Porcetanje X: 3.2080866295954436 %
Porcetanje Y: 34.066834144900895 %
Porcetanje X: 34.066834144900895 %
Porcetanje X: 12.311280744991214 %
Porcetanje X: 20.675149942459704 %
####################
data/resumes/temp/images_resumes_93576192.pdf_rectangles
1_ARTS_93576192_rectangles.jpeg
data/resumes/temp/images_resumes_93576192.pdf/1_ARTS_93576192.jpeg
data/resumes/temp/images_resumes_93576192.pdf_rectangles/1_ARTS_93576192_rectangles.jpeg
data/resumes/temp/images_resumes_93576192.pdf_rectangles/cuts_1_ARTS_93576192
Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 64.9057628690955 %
Porcetanje X: 64.9057628690955 %
Porcetanje X: 11.074503756341683 %
Porcetanje X: 7.80768083477791 %
Porcetanje X: 4.279402163621026 %
Porcetanje X: 6.557023657073086 %
Porcetanje X: 5.932477225564577 %
Porcetanje X: 13.5

Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 2.05469837364244 %
Porcetanje X: 2.05469837364244 %
Porcetanje X: 1.9153171072792115 %
Porcetanje Y: 32.4912630127807 %
Porcetanje X: 32.4912630127807 %
Porcetanje X: 2.0513007483549037 %
Porcetanje X: 1.7469670504010606 %
Porcetanje X: 2.990448244855474 %
####################
data/resumes/temp/images_resumes_33344933.pdf_rectangles
1_ARTS_33344933_rectangles.jpeg
data/resumes/temp/images_resumes_33344933.pdf/1_ARTS_33344933.jpeg
data/resumes/temp/images_resumes_33344933.pdf_rectangles/1_ARTS_33344933_rectangles.jpeg
data/resumes/temp/images_resumes_33344933.pdf_rectangles/cuts_1_ARTS_33344933
Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 55.3850829599946 %
Porcetanje X: 55.3850829599946 %
Porcetanje X: 1.5812655686557024 %
Porcetanje X: 4.464748623734146 %
Porcetanje X: 1.5067330090594513 %
Porcetanje X: 2.8724211155003885 %
Porcetanje X: 1.6514941936611651 %
Porcetanje X: 5.8519688

Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 14.988576364380373 %
Porcetanje X: 14.988576364380373 %
Porcetanje X: 12.46982279708074 %
####################
data/resumes/temp/images_resumes_81508860.pdf_rectangles
1_DIGITAL-MEDIA_81508860_rectangles.jpeg
data/resumes/temp/images_resumes_81508860.pdf/1_DIGITAL-MEDIA_81508860.jpeg
data/resumes/temp/images_resumes_81508860.pdf_rectangles/1_DIGITAL-MEDIA_81508860_rectangles.jpeg
data/resumes/temp/images_resumes_81508860.pdf_rectangles/cuts_1_DIGITAL-MEDIA_81508860
Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 4.629999020027201 %
Porcetanje X: 4.629999020027201 %
Porcetanje Y: 10.812774872438 %
Porcetanje Y: 18.14257412368581 %
Porcetanje Y: 10.936297795193632 %
Porcetanje Y: 28.378634176154083 %
Porcetanje X: 28.378634176154083 %
2_DIGITAL-MEDIA_81508860_rectangles.jpeg
data/resumes/temp/images_resumes_81508860.pdf/2_DIGITAL-MEDIA_81508860.jpeg
data/resumes/temp/images_resumes_81508

...

3_BUSINESS-DEVELOPMENT_12230301_rectangles.jpeg
data/resumes/temp/images_resumes_12230301.pdf/3_BUSINESS-DEVELOPMENT_12230301.jpeg
data/resumes/temp/images_resumes_12230301.pdf_rectangles/3_BUSINESS-DEVELOPMENT_12230301_rectangles.jpeg
data/resumes/temp/images_resumes_12230301.pdf_rectangles/cuts_3_BUSINESS-DEVELOPMENT_12230301
Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 3.424632477093136 %
Porcetanje X: 3.424632477093136 %
Porcetanje X: 3.271304807296295 %
Porcetanje Y: 7.252692607694375 %
Porcetanje X: 7.252692607694375 %
Porcetanje X: 7.0799144642660865 %
####################
data/resumes/temp/images_resumes_15746146.pdf_rectangles
1_APPAREL_15746146_rectangles.jpeg
data/resumes/temp/images_resumes_15746146.pdf/1_APPAREL_15746146.jpeg
data/resumes/temp/images_resumes_15746146.pdf_rectangles/1_APPAREL_15746146_rectangles.jpeg
data/resumes/temp/images_resumes_15746146.pdf_rectangles/cuts_1_APPAREL_15746146
Altura imagen: 5848
Ancho imagen: 4132
Area imag

Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
####################
data/resumes/temp/images_resumes_23185829.pdf_rectangles
1_CHEF_23185829_rectangles.jpeg
data/resumes/temp/images_resumes_23185829.pdf/1_CHEF_23185829.jpeg
data/resumes/temp/images_resumes_23185829.pdf_rectangles/1_CHEF_23185829_rectangles.jpeg
data/resumes/temp/images_resumes_23185829.pdf_rectangles/cuts_1_CHEF_23185829
Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 38.11743252423777 %
Porcetanje X: 38.11743252423777 %
Porcetanje X: 3.2335626116539955 %
Porcetanje Y: 4.737166991337835 %
Porcetanje X: 4.737166991337835 %
Porcetanje X: 4.576721275871613 %
Porcetanje Y: 5.798641413385634 %
Porcetanje X: 5.798641413385634 %
Porcetanje X: 3.3152008017236927 %
Porcetanje Y: 8.416430998658496 %
Porcetanje X: 8.416430998658496 %
Porcetanje X: 4.737601523195559 %
Porcetanje Y: 2.327551273103852 %
Porcetanje X: 2.327551273103852 %
Porcetanje X: 2.1695058288517233 %
Porcetanje Y: 7.14804

Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 2.573545965359286 %
Porcetanje X: 2.573545965359286 %
Porcetanje X: 2.5052210037305183 %
Porcetanje Y: 7.47403485922161 %
Porcetanje X: 7.47403485922161 %
Porcetanje X: 5.8339667842192595 %
Porcetanje Y: 1.8782122250282405 %
Porcetanje X: 1.8782122250282405 %
Porcetanje X: 1.8056660967815839 %
####################
data/resumes/temp/images_resumes_11137306.pdf_rectangles
1_AVIATION_11137306_rectangles.jpeg
data/resumes/temp/images_resumes_11137306.pdf/1_AVIATION_11137306.jpeg
data/resumes/temp/images_resumes_11137306.pdf_rectangles/1_AVIATION_11137306_rectangles.jpeg
data/resumes/temp/images_resumes_11137306.pdf_rectangles/cuts_1_AVIATION_11137306
Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 67.88459049055584 %
Porcetanje X: 67.88459049055584 %
Porcetanje X: 5.893410742355881 %
Porcetanje X: 1.548820523278989 %
Porcetanje X: 10.80751496776022 %
Porcetanje X: 1.548820523278989 %
Porce

Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 4.797852469067953 %
Porcetanje X: 4.797852469067953 %
Porcetanje Y: 5.450767623287862 %
Porcetanje X: 5.450767623287862 %
Porcetanje Y: 6.567324131300464 %
Porcetanje Y: 4.905430141844441 %
Porcetanje Y: 11.307176943358897 %
Porcetanje Y: 18.310601385469653 %
Porcetanje Y: 11.061149143914303 %
Porcetanje X: 11.061149143914303 %
2_ACCOUNTANT_28298773_rectangles.jpeg
data/resumes/temp/images_resumes_28298773.pdf/2_ACCOUNTANT_28298773.jpeg
data/resumes/temp/images_resumes_28298773.pdf_rectangles/2_ACCOUNTANT_28298773_rectangles.jpeg
data/resumes/temp/images_resumes_28298773.pdf_rectangles/cuts_2_ACCOUNTANT_28298773
Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 7.502006295663091 %
Porcetanje X: 7.502006295663091 %
Porcetanje X: 7.327945248654855 %
####################
data/resumes/temp/images_resumes_21794875.pdf_rectangles
1_ACCOUNTANT_21794875_rectangles.jpeg
data/resumes/temp/images_r

Porcetanje X: 16.946258258588337 %
Porcetanje X: 2.0164595701627417 %
Porcetanje Y: 19.25400315577727 %
Porcetanje X: 19.25400315577727 %
Porcetanje X: 19.04857304704002 %
Porcetanje X: 3.1226204207791315 %
Porcetanje X: 3.0437425426056417 %
2_AUTOMOBILE_22732234_rectangles.jpeg
data/resumes/temp/images_resumes_22732234.pdf/2_AUTOMOBILE_22732234.jpeg
data/resumes/temp/images_resumes_22732234.pdf_rectangles/2_AUTOMOBILE_22732234_rectangles.jpeg
data/resumes/temp/images_resumes_22732234.pdf_rectangles/cuts_2_AUTOMOBILE_22732234
Altura imagen: 5848
Ancho imagen: 4132
Area imagen: 24163936
Porcetanje Y: 10.154835702263075 %
Porcetanje X: 10.154835702263075 %
Porcetanje X: 9.97291169782936 %


In [8]:
!pip install datefinder

In [9]:
new_s = """

Beene | six month 2003
Now in 7"" semester of B.Tech course in Mechanical Engineering (2011-2015) from Skyline Institute of
Engineering & Technology (SIET), Greater Noida approved by AICTE, accredited by NBA.
may 2,2011 to oct 8 2022, 
"""


import datefinder

matches = datefinder.find_dates(new_s)

for match in matches:
    print(match)

2003-12-01 00:00:00
2011-05-02 00:00:00
2022-10-08 00:00:00
